#Projet Data Management – BikeShare

## Objectif du projet
L’objectif de ce projet est d’explorer, nettoyer et analyser le dataset BikeShare afin d’identifier les principales tendances d’utilisation du service de vélos partagés et de les présenter à travers des visualisations interactives.


### Importation des librairies

In [2]:
import pandas as pd
import numpy as np


### Chargement du dataset

In [3]:
df = pd.read_csv("data/bikeshare dataset.csv")


In [4]:
df.head()

ride_id  rideable_type           started_at             ended_at  \
0  0A1B623926EF4E16    docked_bike  2021-07-02 14:44:36  2021-07-02 15:19:58   
1  B2D5583A5A5E76EE   classic_bike  2021-07-07 16:57:42  2021-07-07 17:16:09   
2  6F264597DDBF427A   classic_bike  2021-07-25 11:30:55  2021-07-25 11:48:45   
3  379B58EAB20E8AA5   classic_bike  2021-07-08 22:08:30  2021-07-08 22:23:32   
4  6615C1E4EB08E8FB  electric_bike  2021-07-28 16:08:06  2021-07-28 16:27:09   

             start_station_name start_station_id  \
0  Michigan Ave & Washington St            13001   
1    California Ave & Cortez St            17660   
2          Wabash Ave & 16th St           SL-012   
3    California Ave & Cortez St            17660   
4    California Ave & Cortez St            17660   

                 end_station_name end_station_id  start_lat  start_lng  \
0    Halsted St & North Branch St   KA1504000117  41.883984 -87.624684   
1            Wood St & Hubbard St          13432  41.900363 -87.696704   
2            Rush St & Hubbard St   KA1503000044  41.860384 -87.625813   
3         Carpenter St & Huron St          13196  41.900363 -87.696704   
4  Elizabeth (May) St & Fulton St          13197  41.900350 -87.696682   

     end_lat    end_lng member_casual  
0  41.899368 -87.648480        casual  
1  41.889899 -87.671473        casual  
2  41.890173 -87.626185        member  
3  41.894556 -87.653449        member  
4  41.886593 -87.658387        casual

# 1. Analyse exploratoire des données (EDA)


### Dimensions du dataset

In [5]:
df.shape

(822410, 13)

### Structure du dataset

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 822410 entries, 0 to 822409
Data columns (total 13 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   ride_id             822410 non-null  object 
 1   rideable_type       822410 non-null  object 
 2   started_at          822410 non-null  object 
 3   ended_at            822410 non-null  object 
 4   start_station_name  735147 non-null  object 
 5   start_station_id    735148 non-null  object 
 6   end_station_name    729252 non-null  object 
 7   end_station_id      729252 non-null  object 
 8   start_lat           822410 non-null  float64
 9   start_lng           822410 non-null  float64
 10  end_lat             821679 non-null  float64
 11  end_lng             821679 non-null  float64
 12  member_casual       822410 non-null  object 
dtypes: float64(4), object(9)
memory usage: 81.6+ MB


- Le dataset contient 822 410 lignes et 13 colonnes.
- Plusieurs variables présentent des valeurs manquantes : `start_station_name`, `start_station_id`, `end_station_name`, `end_station_id`, ainsi que `end_lat` et `end_lng`.
- Les colonnes `started_at` et `ended_at` sont de type `object` alors qu’elles représentent des dates/heures : elles devront être converties en `datetime` pour permettre les analyses temporelles (durée de trajet, heure, jour, mois…).

### Statistiques descriptives des variables numériques

In [7]:
df.describe()

start_lat      start_lng        end_lat        end_lng
count  822410.000000  822410.000000  821679.000000  821679.000000
mean       41.903565     -87.645536      41.903815     -87.645662
std         0.043153       0.026856       0.043289       0.027065
min        41.648501     -87.840000      41.630000     -87.850000
25%        41.883380     -87.659660      41.883380     -87.659753
50%        41.900219     -87.641170      41.900960     -87.641170
75%        41.929143     -87.627691      41.929505     -87.627680
max        42.070000     -87.520000      42.150000     -87.490000

Les statistiques descriptives montrent que les coordonnées géographiques
(start_lat, start_lng, end_lat, end_lng) sont cohérentes et correspondent
à une zone géographique restreinte. Les valeurs minimales et maximales
restent réalistes, ce qui indique l’absence de valeurs aberrantes
évidentes dans les données de localisation.

### Analyse des variables catégorielles


In [8]:
df['member_casual'].value_counts()

member_casual
casual    442056
member    380354
Name: count, dtype: int64

In [9]:
df['rideable_type'].value_counts()

rideable_type
classic_bike     506909
electric_bike    257803
docked_bike       57698
Name: count, dtype: int64

L’analyse des variables catégorielles montre une répartition relativement équilibrée
entre les utilisateurs occasionnels (casual) et les abonnés (member), avec une légère
prédominance des utilisateurs occasionnels. En revanche, la variable `rideable_type`
présente une distribution plus déséquilibrée : les vélos classiques sont majoritaires,
suivis des vélos électriques, tandis que les vélos de type `docked_bike` sont nettement
moins représentés, ce qui suggère un usage plus marginal ou un déploiement plus limité
de ce type de vélo.

### Analyse préliminaire des variables temporelles

In [10]:
df[["started_at", "ended_at"]].head()


started_at             ended_at
0  2021-07-02 14:44:36  2021-07-02 15:19:58
1  2021-07-07 16:57:42  2021-07-07 17:16:09
2  2021-07-25 11:30:55  2021-07-25 11:48:45
3  2021-07-08 22:08:30  2021-07-08 22:23:32
4  2021-07-28 16:08:06  2021-07-28 16:27:09

Les variables `started_at` et `ended_at` représentent des informations
temporelles mais sont actuellement stockées sous forme de chaînes de
caractères. Une inspection préliminaire des premières valeurs permet de
confirmer leur format et leur cohérence avant la conversion en type
datetime.

# 2. Nettoyage des données

## 2.1 Diagnostic des problèmes de qualité des données

### Valeurs manquantes

In [11]:
df.isna().sum()

ride_id                   0
rideable_type             0
started_at                0
ended_at                  0
start_station_name    87263
start_station_id      87262
end_station_name      93158
end_station_id        93158
start_lat                 0
start_lng                 0
end_lat                 731
end_lng                 731
member_casual             0
dtype: int64

Des valeurs manquantes sont présentes dans les variables liées aux stations
de départ et d’arrivée ainsi que dans les coordonnées de fin de trajet.

### Valeurs dupliquées

In [12]:
df.duplicated().sum()

np.int64(0)


Aucune observation dupliquée n’a été détectée dans le dataset.

### Incohérences temporelles

In [13]:
df_temp = df.copy()     ##pour tester sans toucher a l'original
df_temp["started_at"] = pd.to_datetime(df_temp["started_at"], errors="coerce")  ##Convertit (object) en date/heure (datetime)
df_temp["ended_at"] = pd.to_datetime(df_temp["ended_at"], errors="coerce")  ##errors="coerce": Si une valeur ne peut pas être convertie devient NaT
(df_temp["ended_at"] < df_temp["started_at"]).sum()  ##nombre total de trajets incohérents


np.int64(13)

Un faible nombre d’observations présente une incohérence temporelle,
où la date de fin du trajet est antérieure à la date de début.

### Les outliers

Les statistiques descriptives de la durée des trajets montrent que la
majorité des trajets dure entre quelques minutes et une vingtaine de
minutes. Toutefois, la présence de durées négatives ainsi que de durées
extrêmement élevées indique des incohérences temporelles et des valeurs
aberrantes qui ne sont pas réalistes pour des trajets à vélo.

In [14]:

df_temp["trip_duration_min"] = (df_temp["ended_at"] - df_temp["started_at"]).dt.total_seconds()/60
df_temp["trip_duration_min"].describe()


count    822410.000000
mean         24.210642
std         214.191034
min          -0.200000
25%           7.583333
50%          13.350000
75%          23.733333
max       49107.150000
Name: trip_duration_min, dtype: float64

Afin d’analyser les valeurs aberrantes liées aux trajets, une variable
`trip_duration_min` représentant la durée du trajet en minutes a été créée
à partir des dates de début (`started_at`) et de fin (`ended_at`).


In [15]:
import plotly.express as px

# Filtrage pour la visualisation (diagnostic, pas encore nettoyage final)
df_visu = df_temp[
    (df_temp["trip_duration_min"] >= 0) &
    (df_temp["trip_duration_min"] <= 120)
]

fig = px.histogram(
    df_visu,
    x="trip_duration_min",
    nbins=40,
    histnorm="probability density",
    opacity=0.8,
    title="Histogramme (densité) de la durée des trajets (0–120 minutes)"
)

fig.show()


Un histogramme en densité de la durée des trajets, limité à une plage de
durées réalistes (0–120 minutes), permet de visualiser la distribution
globale. La distribution est fortement asymétrique à droite, avec une
forte concentration de trajets courts et une longue traîne de durées plus
élevées.


In [16]:
df[["start_lat", "start_lng", "end_lat", "end_lng"]].describe()


start_lat      start_lng        end_lat        end_lng
count  822410.000000  822410.000000  821679.000000  821679.000000
mean       41.903565     -87.645536      41.903815     -87.645662
std         0.043153       0.026856       0.043289       0.027065
min        41.648501     -87.840000      41.630000     -87.850000
25%        41.883380     -87.659660      41.883380     -87.659753
50%        41.900219     -87.641170      41.900960     -87.641170
75%        41.929143     -87.627691      41.929505     -87.627680
max        42.070000     -87.520000      42.150000     -87.490000

Les statistiques descriptives des coordonnées géographiques
(start_lat, start_lng, end_lat, end_lng) montrent des valeurs minimales
et maximales cohérentes avec la zone géographique étudiée. Aucune valeur
aberrante problématique n’a été identifiée pour ces variables.

### Conclusion pour les outliers:
L’analyse des valeurs aberrantes montre que les outliers significatifs
concernent uniquement la durée des trajets. Des incohérences temporelles
(durées négatives) ainsi que des durées extrêmement élevées ont été
identifiées et seront traitées lors de la phase de nettoyage. Les autres
variables du dataset ne présentent pas de valeurs aberrantes nécessitant
un traitement particulier.


## 2.2 Actions de nettoyage appliquées

### 2.2.1 Conversion des variables temporelles

In [42]:
df["started_at"] = pd.to_datetime(df["started_at"], errors="coerce")
df["ended_at"]   = pd.to_datetime(df["ended_at"], errors="coerce")


In [43]:
df[["started_at", "ended_at"]].dtypes

started_at    datetime64[ns]
ended_at      datetime64[ns]
dtype: object

Les variables temporelles `started_at` et `ended_at`, initialement stockées
sous forme de chaînes de caractères, ont été converties en format datetime
afin de permettre des comparaisons temporelles fiables et le calcul de la
durée des trajets.


### 2.2.2 Gestion des valeurs manquantes

Sur base des problèmes identifiés lors du diagnostic, des règles de
nettoyage ont été définies et appliquées afin d’améliorer la cohérence
et la fiabilité du dataset.

In [17]:

df = df.dropna(subset=["end_lat", "end_lng"])


Les coordonnées géographiques de fin de trajet (`end_lat`, `end_lng`)
présentent un nombre très limité de valeurs manquantes (731 observations,
soit moins de 0,1 % du dataset). Ces lignes ont été supprimées afin de
garantir la cohérence spatiale des trajets, sans recourir à une imputation
de coordonnées.


In [18]:
df = df.drop(columns=["start_station_id", "end_station_id"])
df.head()


ride_id  rideable_type           started_at             ended_at  \
0  0A1B623926EF4E16    docked_bike  2021-07-02 14:44:36  2021-07-02 15:19:58   
1  B2D5583A5A5E76EE   classic_bike  2021-07-07 16:57:42  2021-07-07 17:16:09   
2  6F264597DDBF427A   classic_bike  2021-07-25 11:30:55  2021-07-25 11:48:45   
3  379B58EAB20E8AA5   classic_bike  2021-07-08 22:08:30  2021-07-08 22:23:32   
4  6615C1E4EB08E8FB  electric_bike  2021-07-28 16:08:06  2021-07-28 16:27:09   

             start_station_name                end_station_name  start_lat  \
0  Michigan Ave & Washington St    Halsted St & North Branch St  41.883984   
1    California Ave & Cortez St            Wood St & Hubbard St  41.900363   
2          Wabash Ave & 16th St            Rush St & Hubbard St  41.860384   
3    California Ave & Cortez St         Carpenter St & Huron St  41.900363   
4    California Ave & Cortez St  Elizabeth (May) St & Fulton St  41.900350   

   start_lng    end_lat    end_lng member_casual  
0 -87.624684  41.899368 -87.648480        casual  
1 -87.696704  41.889899 -87.671473        casual  
2 -87.625813  41.890173 -87.626185        member  
3 -87.696704  41.894556 -87.653449        member  
4 -87.696682  41.886593 -87.658387        casual

Les colonnes `start_station_id` et `end_station_id` correspondent à des
identifiants techniques et n’apportent pas de valeur analytique directe
dans le cadre des analyses retenues. Elles ont donc été supprimées afin
de simplifier le jeu de données.

In [19]:
df[['start_station_name', 'end_station_name']] = (
    df[['start_station_name', 'end_station_name']]
    .fillna('Missing')
)

Les variables `start_station_name` et `end_station_name` sont des variables
qualitatives pour lesquelles une imputation numérique ou par la modalité la plus
fréquente n’est pas pertinente. Afin de conserver les observations tout en
signalant explicitement l’absence d’information, les valeurs manquantes ont été
remplacées par la modalité `"Missing"`.

Le traitement des valeurs manquantes a été réalisé selon la nature et la
pertinence des variables. Les colonnes jugées non essentielles à l’analyse ont
été supprimées, les observations présentant des coordonnées géographiques
incomplètes ont été retirées, et les variables catégorielles ont été imputées par
une modalité explicite `"Missing"`. Ces choix permettent de préserver la qualité,
la cohérence et l’exploitabilité du jeu de données pour les analyses ultérieures.


### 2.2.3 Correction des incohérences temporelles

In [38]:
df = df[df["ended_at"] >= df["started_at"]]


In [39]:
(df["ended_at"] < df["started_at"]).sum()


np.int64(0)

Certaines observations présentent une incohérence temporelle, où la date
de fin du trajet est antérieure à la date de début, entraînant des durées
négatives. Ces situations étant irréalistes et ne pouvant pas être
corrigées de manière fiable, les lignes concernées ont été supprimées du
jeu de données afin de garantir la cohérence temporelle des trajets.

### 2.2.4 Traitement des outliers

In [50]:
df["trip_duration_min"] = (df["ended_at"] - df["started_at"]).dt.total_seconds() / 60


Pour identifier et traiter les valeurs aberrantes liées à la durée des trajets, une nouvelle variable `trip_duration_min` est créée. Elle correspond à la durée de chaque trajet en minutes, calculée à partir de la différence entre `ended_at` et `started_at`.


In [51]:
# Définition d'un seuil maximal réaliste (24 heures)
MAX_DURATION = 24 * 60  # 1440 minutes


# Suppression des trajets avec durée excessive
df = df[df["trip_duration_min"] <= MAX_DURATION]


La distribution de la durée contient des valeurs extrêmes (durées irréalistes). Un seuil maximal de 24 heures (1440 minutes) est fixé afin de limiter l’impact de ces valeurs aberrantes. Les trajets dont la durée dépasse ce seuil sont supprimés, car ils risquent de biaiser les analyses.


In [52]:
df["trip_duration_min"].describe()


count    821467.000000
mean         21.187414
std          35.235854
min           0.000000
25%           7.583333
50%          13.333333
75%          23.683333
max        1425.000000
Name: trip_duration_min, dtype: float64

# 3. Création de nouvelles variables


### 3.1 Variable de durée du trajet (déjà créée)

In [ ]:
df["trip_duration_min"] = (df["ended_at"] - df["started_at"]).dt.total_seconds() / 60

Une première variable dérivée, `trip_duration_min`, a déjà été créée lors de la phase
de nettoyage des données. Elle représente la durée de chaque trajet en minutes,
calculée à partir de la différence entre les dates de début (`started_at`) et de fin
(`ended_at`). Cette variable sera utilisée dans les analyses et les visualisations
afin d’étudier les comportements d’utilisation du service.


### 3.2 Création de la variable day_of_week

In [53]:
df["day_of_week"] = df["started_at"].dt.day_name()


Afin d’analyser l’utilisation du service selon les jours de la semaine, une variable
`day_of_week` est créée à partir de la date de début du trajet. Cette variable permet
d’identifier les jours où la demande est la plus élevée et de comparer les usages entre
les jours ouvrables et le week-end.


### 3.3 Création de la variable start_hour

In [54]:
df["start_hour"] = df["started_at"].dt.hour


Dans le but d’étudier les périodes de la journée où le service de vélos est le plus
utilisé, une variable `start_hour` est créée. Elle correspond à l’heure de début du
trajet, extraite de la variable `started_at`, et permet d’analyser les heures de forte
utilisation du service.


In [55]:
df.head()

ride_id  rideable_type          started_at            ended_at  \
0  0A1B623926EF4E16    docked_bike 2021-07-02 14:44:36 2021-07-02 15:19:58   
1  B2D5583A5A5E76EE   classic_bike 2021-07-07 16:57:42 2021-07-07 17:16:09   
2  6F264597DDBF427A   classic_bike 2021-07-25 11:30:55 2021-07-25 11:48:45   
3  379B58EAB20E8AA5   classic_bike 2021-07-08 22:08:30 2021-07-08 22:23:32   
4  6615C1E4EB08E8FB  electric_bike 2021-07-28 16:08:06 2021-07-28 16:27:09   

             start_station_name                end_station_name  start_lat  \
0  Michigan Ave & Washington St    Halsted St & North Branch St  41.883984   
1    California Ave & Cortez St            Wood St & Hubbard St  41.900363   
2          Wabash Ave & 16th St            Rush St & Hubbard St  41.860384   
3    California Ave & Cortez St         Carpenter St & Huron St  41.900363   
4    California Ave & Cortez St  Elizabeth (May) St & Fulton St  41.900350   

   start_lng    end_lat    end_lng member_casual  trip_duration_min  \
0 -87.624684  41.899368 -87.648480        casual          35.366667   
1 -87.696704  41.889899 -87.671473        casual          18.450000   
2 -87.625813  41.890173 -87.626185        member          17.833333   
3 -87.696704  41.894556 -87.653449        member          15.033333   
4 -87.696682  41.886593 -87.658387        casual          19.050000   

  day_of_week  start_hour  
0      Friday          14  
1   Wednesday          16  
2      Sunday          11  
3    Thursday          22  
4   Wednesday          16

# 4. Visualisation des tendances

### 4.1 Utilisation du service selon l’heure de départ (start_hour)


In [66]:
import plotly.express as px

# Comptage du nombre de trajets par heure de départ
trips_by_hour = (
    df.groupby("start_hour")
    .size()
    .reset_index(name="Nombre de trajets")
)

fig = px.bar(
    trips_by_hour,
    x="start_hour",
    y="Nombre de trajets",
    title="Nombre de trajets par heure de départ",
    labels={
        "start_hour": "Heure de départ",
        "Nombre de trajets": "Nombre de trajets"
    },
    color="Nombre de trajets",
    color_continuous_scale="Blues"
)

fig.update_layout(
    plot_bgcolor="white",
    title_x=0.5,
    xaxis=dict(tickmode="linear")
)

fig.show()




Ce graphique représente la distribution du nombre de trajets en fonction de l’heure de départ, sur une plage horaire allant de 0 à 23 heures. L’axe horizontal correspond aux heures de la journée, tandis que l’axe vertical indique le nombre total de trajets enregistrés pour chaque heure.

📌 Interprétation

On observe que le nombre de trajets est relativement faible durant la nuit et en début de matinée. À partir de 6h, l’utilisation du service augmente progressivement, avec une forte concentration des trajets en fin d’après-midi. Un pic d’utilisation est clairement visible autour de 17h, indiquant que le service est particulièrement sollicité à cette heure-là. Cette dynamique suggère que les vélos sont majoritairement utilisés pour des déplacements quotidiens, notamment liés aux horaires de travail ou de retour à domicile. Après 18h, le nombre de trajets diminue progressivement en soirée.

### 4.2 Nombre de trajets par jour de la semaine

In [58]:
fig = px.bar(
    day_counts,
    x="Jour de la semaine",
    y="Nombre de trajets",
    title="Nombre de trajets par jour de la semaine",
    color="Jour de la semaine",
    color_discrete_map={
        "Monday": "#4C72B0",
        "Tuesday": "#4C72B0",
        "Wednesday": "#4C72B0",
        "Thursday": "#4C72B0",
        "Friday": "#4C72B0",
        "Saturday": "#DD8452",
        "Sunday": "#DD8452"
    }
)

fig.update_layout(
    plot_bgcolor="white",
    title_x=0.5
)

fig.show()



Ce graphique représente le nombre total de trajets effectués en fonction du jour
de la semaine. Il permet d’identifier les différences d’utilisation du service
entre les jours ouvrables et le week-end.


📌 Interprétation

On observe que l’utilisation du service varie selon le jour de la semaine.
Les jours du week-end, en particulier le samedi, enregistrent le plus grand
nombre de trajets. Cela suggère un usage davantage orienté vers les loisirs
et les déplacements personnels.

En revanche, les jours de semaine présentent des volumes plus modérés et
relativement stables, ce qui indique une utilisation plus régulière liée
aux déplacements quotidiens, comme le travail ou les études.


### 4.3 Répartition des trajets selon le type de vélo

In [63]:
import plotly.express as px

# Comptage du nombre de trajets par type de vélo
bike_type_counts = (
    df["rideable_type"]
    .value_counts()
    .reset_index()
)

bike_type_counts.columns = ["Type de vélo", "Nombre de trajets"]

fig = px.bar(
    bike_type_counts,
    x="Type de vélo",
    y="Nombre de trajets",
    color="Type de vélo",
    title="Répartition des trajets selon le type de vélo",
    labels={
        "Type de vélo": "Type de vélo",
        "Nombre de trajets": "Nombre de trajets"
    }
)

fig.update_layout(
    plot_bgcolor="white",
    title_x=0.5
)

fig.show()



Ce graphique représente la répartition du nombre total de trajets en fonction
du type de vélo utilisé. Il permet d’identifier quels types de vélos sont les
plus fréquemment utilisés par les usagers du service.


📌 Interprétation

On observe que les vélos classiques sont les plus utilisés, suivis par les vélos
électriques. Les vélos de type docked_bike sont nettement moins représentés,
ce qui peut s’expliquer par une disponibilité plus limitée ou un usage plus
spécifique.

Cette répartition suggère que les utilisateurs privilégient majoritairement
les vélos classiques et électriques pour leurs déplacements quotidiens.





### 4.4 Heatmap de l’utilisation du service selon l’heure et le jour

In [62]:
import plotly.express as px

# Création de la table croisée : nombre de trajets par jour et par heure
heatmap_data = (
    df.groupby(["day_of_week", "start_hour"])
    .size()
    .reset_index(name="n_trips")
)

# Ordre logique des jours
order_days = ["Monday", "Tuesday", "Wednesday", "Thursday", "Friday", "Saturday", "Sunday"]

fig = px.density_heatmap(
    heatmap_data,
    x="start_hour",
    y="day_of_week",
    z="n_trips",
    category_orders={"day_of_week": order_days},
    color_continuous_scale="Blues",
    title="Intensité des trajets selon l’heure et le jour de la semaine",
    labels={
        "start_hour": "Heure de départ",
        "day_of_week": "Jour de la semaine",
        "n_trips": "Nombre de trajets"
    }
)

fig.update_layout(
    plot_bgcolor="white",
    title_x=0.5
)

fig.show()


Cette heatmap illustre l’intensité des trajets en fonction de l’heure de départ
et du jour de la semaine. Les couleurs plus foncées indiquent un nombre plus
élevé de trajets, permettant d’identifier rapidement les périodes de forte
utilisation du service.

📌 Interprétation

On observe une forte concentration des trajets en fin d’après-midi, notamment
entre 15h et 18h, surtout durant les jours de semaine, ce qui correspond aux
heures de sortie du travail ou des études. Le vendredi présente une intensité
particulièrement élevée sur ces créneaux.

Le week-end, l’utilisation est plus étalée sur la journée, avec des pics plus
précoces le samedi, suggérant un usage davantage orienté vers les loisirs.
Cette visualisation met clairement en évidence des comportements d’utilisation
différents selon le jour et l’heure.

